In [1]:
import pandas as pd
import folium
import numpy as np
from math import radians, cos, sin, asin, sqrt
from ipyleaflet import Map, Marker, Popup, Icon
import ipywidgets as widgets
from IPython.display import display

<h1>Speed Flows<h1>

In [5]:
file_path = 'C:/Users/migue/source/repos/DataScience/datasets/speed_flow/march/intensiteit-snelheid-export 1 maart_metadata.zip'
# Define the columns to load
cols_to_load = ['id_meetlocatie', 'start_locatie_longitude', 'start_locatie_latitude', 'wegnaam_vild', 'rijstrook_rijbaan']
cols_for_uniqueness = ['id_meetlocatie', 'start_locatie_longitude', 'start_locatie_latitude']
# Initialize an empty DataFrame to hold unique rows
unique_rows = pd.DataFrame(columns=cols_to_load)

# Set chunk size
chunk_size = 20000

# Read the CSV file in chunks
for chunk in pd.read_csv(file_path, usecols=cols_to_load, chunksize=chunk_size):
    # Drop duplicates within the chunk
    chunk_unique = chunk.drop_duplicates(subset=cols_to_load)
    
    # Concatenate the unique rows from this chunk with the main DataFrame, and drop duplicates again
    unique_rows = pd.concat([unique_rows, chunk_unique]).drop_duplicates(subset=cols_for_uniqueness)

# Print the size of the reduced DataFrame
print(unique_rows.shape)
unique_rows.head()

C:\Users\migue\AppData\Local\Temp\ipykernel_27520\695956152.py:17: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  unique_rows = pd.concat([unique_rows, chunk_unique]).drop_duplicates(subset=cols_for_uniqueness)
C:\Users\migue\AppData\Local\Temp\ipykernel_27520\695956152.py:12: DtypeWarning: Columns (40) have mixed types. Specify dtype option on import or set low_memory=False.
  for chunk in pd.read_csv(file_path, usecols=cols_to_load, chunksize=chunk_size):
C:\Users\migue\AppData\Local\Temp\ipykernel_27520\695956152.py:12: DtypeWarning: Columns (40) have mixed types. Specify dtype option on import or set low_memory=False.
  for chunk in pd.read_csv(file_path, usecols=cols_to_load, chunksize=chunk_size):
C:\Users\migue\AppData\Local\Temp\ipyk

(1452, 5)


id_meetlocatie  start_locatie_longitude  start_locatie_latitude  \
0      GEO0B_R_RWSTI356574                  4.36867                51.91099   
17280  GEO0B_R_RWSTI357017                  4.33028                51.91749   
34560  GEO0B_R_RWSTI357030                  4.33322                51.91892   
43200  GEO0B_R_RWSTI357031                  4.33499                51.91891   
51840  GEO0B_R_RWSTI357032                  4.32780                51.91782   

         wegnaam_vild rijstrook_rijbaan  
0      Ring Rotterdam             lane1  
17280             NaN             lane1  
34560             NaN             lane1  
43200             NaN             lane1  
51840             NaN             lane1

In [6]:
# filter so that only rows where wegnaam_vild equals 'Rotterdam Ring' are included
unique_rows = unique_rows[unique_rows['wegnaam_vild'] == 'Ring Rotterdam']
print('Rows:', len(unique_rows))

# Convert coordinates to floats
unique_rows['start_locatie_longitude'] = pd.to_numeric(unique_rows['start_locatie_longitude'], errors='coerce')
unique_rows['start_locatie_latitude'] = pd.to_numeric(unique_rows['start_locatie_latitude'], errors='coerce')

# Drop rows with NaN values in 'primaire_locatie_lengtegraad' or 'primaire_locatie_breedtegraad'
unique_rows.dropna(subset=['start_locatie_longitude', 'start_locatie_latitude'], inplace=True)

min_longitude = unique_rows['start_locatie_longitude'].min()
max_longitude = unique_rows['start_locatie_longitude'].max()
min_latitude = unique_rows['start_locatie_latitude'].min()
max_latitude = unique_rows['start_locatie_latitude'].max()

# Truncate to 6 decimal places without rounding using string formatting
min_latitude = float(format(min_latitude))
max_latitude = float(format(max_latitude))
min_longitude = float(format(min_longitude))
max_longitude = float(format(max_longitude))

print(max_latitude)
print(min_latitude)
print(max_longitude)
print(min_longitude)
unique_rows.head()

Rows: 634
51.95385
51.85837
4.59255
4.35371


id_meetlocatie  start_locatie_longitude  start_locatie_latitude  \
0       GEO0B_R_RWSTI356574                 4.368670               51.910990   
103680  GEO0B_R_RWSTI357193                 4.370783               51.910187   
120960  GEO0B_R_RWSTI357194                 4.370130               51.911260   
129600  GEO0B_R_RWSTI357196                 4.373160               51.926146   
138240  GEO0B_R_RWSTI357197                 4.374173               51.926116   

          wegnaam_vild rijstrook_rijbaan  
0       Ring Rotterdam             lane1  
103680  Ring Rotterdam             lane1  
120960  Ring Rotterdam             lane1  
129600  Ring Rotterdam             lane1  
138240  Ring Rotterdam             lane1

In [28]:
def haversine(lon1, lat1, lon2, lat2):
    # Convert decimal degrees to radians
    lon1, lat1, lon2, lat2 = map(radians, [lon1, lat1, lon2, lat2])

    # Haversine formula
    dlon = lon2 - lon1
    dlat = lat2 - lat1
    a = sin(dlat/2)**2 + cos(lat1) * cos(lat2) * sin(dlon/2)**2
    c = 2 * asin(sqrt(a))
    r = 6371 # Radius of earth in kilometers
    return c * r

# Now you can calculate the distances
width_km = haversine(min_longitude, min_latitude, max_longitude, min_latitude)
print(width_km)
height_km = haversine(min_longitude, min_latitude, min_longitude, max_latitude)
print(height_km)

# Perimeter of the rectangle
perimeter_km = 2 * (width_km + height_km)
print(perimeter_km)

16.402286392728197
10.616891596022068
54.03835597750053


In [26]:
# Create a map centered on the mean latitude and longitude
m = folium.Map(location=[unique_rows['start_locatie_latitude'].mean(), unique_rows['start_locatie_longitude'].mean()], zoom_start=10)

# Add a marker for each unique meetlocatie

for i in range(unique_rows.shape[0]):
    folium.Marker([unique_rows['start_locatie_latitude'].iloc[i], unique_rows['start_locatie_longitude'].iloc[i]]).add_to(m)

# Show the map
m.save('unique_meetlocaties.html')
m

<h1>Incidents</h1>

In [7]:
df7 = pd.read_csv('C:/Users/migue/source/repos/DataScience/datasets/status/sb-incidenten-export_rotterdam 1 maart - 31 augustus.zip', compression='zip')
print(df7.columns)
df7.head()

Index(['id', 'versie', 'type', 'bron', 'starttijd', 'eindtijd',
       'situatie_aangemaakt_tijd', 'situatie_versie_tijd', 'speciaal_geval',
       'vild_versie', 'vild_richting', 'vild_primaire_locatie',
       'vild_afstand_tot_primaire_locatie', 'vild_secundaire_locatie',
       'vild_afstand_tot_secundaire_locatie', 'mobiliteit',
       'veiligheids_gerelateerd_bericht', 'primaire_locatie_lengtegraad',
       'primaire_locatie_breedtegraad', 'secundaire_locatie_lengtegraad',
       'secundaire_locatie_breedtegraad', 'gedetailleerd_type'],
      dtype='object')


C:\Users\migue\AppData\Local\Temp\ipykernel_27520\533038565.py:1: DtypeWarning: Columns (16) have mixed types. Specify dtype option on import or set low_memory=False.
  df7 = pd.read_csv('C:/Users/migue/source/repos/DataScience/datasets/status/sb-incidenten-export_rotterdam 1 maart - 31 augustus.zip', compression='zip')


id  versie                 type  bron  \
0  A-ALL-IM19087680NLD_1       2  vehicle_obstruction  ANWB   
1  A-ALL-IM19087680NLD_1       3  vehicle_obstruction  ANWB   
2  A-ALL-IM19087680NLD_1       4  vehicle_obstruction  ANWB   
3  A-ALL-IM19087680NLD_1       5  vehicle_obstruction  ANWB   
4  A-ALL-IM19087680NLD_1       6  vehicle_obstruction  ANWB   

             starttijd             eindtijd situatie_aangemaakt_tijd  \
0  2019-08-28 11:34:31  2020-09-09 14:32:53      2019-08-28 12:11:32   
1  2019-08-28 11:34:31  2020-09-09 14:32:53      2019-09-11 11:49:12   
2  2019-08-28 11:34:31  2020-09-09 14:32:53      2019-12-11 11:32:28   
3  2019-08-28 11:34:31  2019-12-16 18:45:27      2019-12-11 11:32:28   
4  2019-08-28 11:34:31  2020-09-09 14:32:53      2020-06-24 12:40:00   

  situatie_versie_tijd   speciaal_geval vild_versie  ...  \
0  2019-08-28 12:11:32              NaN       5.17A  ...   
1  2019-09-11 11:49:12              NaN       5.18A  ...   
2  2019-12-11 11:32:28              NaN       5.19A  ...   
3  2019-12-11 11:32:28  snapshot_closed       5.19A  ...   
4  2020-06-24 12:40:00              NaN       5.21A  ...   

  vild_afstand_tot_primaire_locatie  vild_secundaire_locatie  \
0                               NaN                   9200.0   
1                               NaN                   9200.0   
2                            4100.0                   9197.0   
3                            4100.0                   9197.0   
4                            4100.0                   9197.0   

   vild_afstand_tot_secundaire_locatie  mobiliteit  \
0                                  NaN  stationary   
1                                  NaN  stationary   
2                                100.0  stationary   
3                                100.0  stationary   
4                                100.0  stationary   

   veiligheids_gerelateerd_bericht primaire_locatie_lengtegraad  \
0                             True                     4.346407   
1                             True                     4.346407   
2                             True                     4.346407   
3                             True                     4.346407   
4                             True                     4.346407   

  primaire_locatie_breedtegraad  secundaire_locatie_lengtegraad  \
0                      52.04192                        4.346407   
1                      52.04192                        4.346407   
2                      52.04192                             NaN   
3                      52.04192                             NaN   
4                      52.04192                             NaN   

   secundaire_locatie_breedtegraad  gedetailleerd_type  
0                         52.04192   brokenDownVehicle  
1                         52.04192   brokenDownVehicle  
2                              NaN   brokenDownVehicle  
3                              NaN   brokenDownVehicle  
4                              NaN   brokenDownVehicle  

[5 rows x 22 columns]

In [8]:
incidents_df = df7[['id', 'starttijd', 'eindtijd', 'type', 'gedetailleerd_type', 'primaire_locatie_lengtegraad', 'primaire_locatie_breedtegraad']]
print(len(incidents_df))
incidents_df.head()

161962


id            starttijd             eindtijd  \
0  A-ALL-IM19087680NLD_1  2019-08-28 11:34:31  2020-09-09 14:32:53   
1  A-ALL-IM19087680NLD_1  2019-08-28 11:34:31  2020-09-09 14:32:53   
2  A-ALL-IM19087680NLD_1  2019-08-28 11:34:31  2020-09-09 14:32:53   
3  A-ALL-IM19087680NLD_1  2019-08-28 11:34:31  2019-12-16 18:45:27   
4  A-ALL-IM19087680NLD_1  2019-08-28 11:34:31  2020-09-09 14:32:53   

                  type gedetailleerd_type  primaire_locatie_lengtegraad  \
0  vehicle_obstruction  brokenDownVehicle                      4.346407   
1  vehicle_obstruction  brokenDownVehicle                      4.346407   
2  vehicle_obstruction  brokenDownVehicle                      4.346407   
3  vehicle_obstruction  brokenDownVehicle                      4.346407   
4  vehicle_obstruction  brokenDownVehicle                      4.346407   

   primaire_locatie_breedtegraad  
0                       52.04192  
1                       52.04192  
2                       52.04192  
3                       52.04192  
4                       52.04192

In [9]:
# Unique IDs
unique_id_count = incidents_df['id'].nunique()
print(f'Unique IDs: {unique_id_count}')

# Convert coordinates to floats
incidents_df['primaire_locatie_lengtegraad'] = pd.to_numeric(incidents_df['primaire_locatie_lengtegraad'], errors='coerce')
incidents_df['primaire_locatie_breedtegraad'] = pd.to_numeric(incidents_df['primaire_locatie_breedtegraad'], errors='coerce')

# Drop rows with NaN values in 'primaire_locatie_lengtegraad' or 'primaire_locatie_breedtegraad'
incidents_df.dropna(subset=['primaire_locatie_lengtegraad', 'primaire_locatie_breedtegraad'], inplace=True)

print('Rows:', len(incidents_df))

Unique IDs: 39304
Rows: 161962


C:\Users\migue\AppData\Local\Temp\ipykernel_27520\388227697.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  incidents_df['primaire_locatie_lengtegraad'] = pd.to_numeric(incidents_df['primaire_locatie_lengtegraad'], errors='coerce')
C:\Users\migue\AppData\Local\Temp\ipykernel_27520\388227697.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  incidents_df['primaire_locatie_breedtegraad'] = pd.to_numeric(incidents_df['primaire_locatie_breedtegraad'], errors='coerce')
C:\Users\migue\AppData\Local\Temp\ipyk

In [10]:
# Filter incidents_df for entries within the bounding box of Ring Rotterdam
incidents_df = incidents_df[
    (incidents_df['primaire_locatie_breedtegraad'] >= min_latitude) & 
    (incidents_df['primaire_locatie_breedtegraad'] <= max_latitude) & 
    (incidents_df['primaire_locatie_lengtegraad'] >= min_longitude) & 
    (incidents_df['primaire_locatie_lengtegraad'] <= max_longitude)
]
print('Rows:', len(incidents_df))

# Convert 'starttijd' and 'eindtijd' to datetime
incidents_df['starttijd'] = pd.to_datetime(incidents_df['starttijd'])
incidents_df['eindtijd'] = pd.to_datetime(incidents_df['eindtijd'])

# Define your date range
start_date = pd.Timestamp('2020-03-01')
end_date = pd.Timestamp('2020-05-31')

# Filter the DataFrame to only include incidents within the specified date range
incidents_df = incidents_df[(incidents_df['starttijd'] >= start_date) & (incidents_df['eindtijd'] <= end_date)]
print('Rows:', len(incidents_df))

incidents_df = incidents_df.drop_duplicates(subset=['id', 'starttijd', 'eindtijd'])
print('Rows:', len(incidents_df))
incidents_df = incidents_df.drop_duplicates(subset='id', keep='last')
print('Rows:', len(incidents_df))


# After filtering within the boundary box, this is another list of coordinates to exclude
exclude_points = [
    (51.922989, 4.471057), (51.918350, 4.484596), (51.922234, 4.496322), (51.911800, 4.463905), (51.900166, 4.468047), (51.895542, 4.494501),
    (51.895172, 4.531459), (51.875618, 4.510518), (51.861649, 4.431097), (51.885815, 4.580630), (51.885921, 4.580412), (51.885960, 4.580658),
    (51.885960, 4.580583), (51.883751, 4.580418), (51.883572, 4.580498), (51.883202, 4.580448), (51.880310, 4.579200), (51.879910, 4.578885),
    (51.945419, 4.530178), (51.945461, 4.530137), (51.945221, 4.5317659), (51.944641, 4.532023), (51.945221, 4.531765), (51.950294, 4.530092),
    (51.952148, 4.534003), (51.952148, 4.534270), (51.952080, 4.534332), (51.950920, 4.529327), (51.950989, 4.528609), (51.940910, 4.485485), 
    (51.940910, 4.485485), (51.941509, 4.485172), (51.941509, 4.485007), (51.941669, 4.484843), (51.949543, 4.353939), (51.948170, 4.354400),
    (51.947891, 4.354633), (51.947689, 4.355468), (51.946350, 4.355833), (51.946320, 4.355840), (51.946209, 4.355927), (51.946266, 4.356325),
    (51.945320, 4.356800), (51.945229, 4.357145), (51.945011, 4.357248), (51.944839, 4.357110), (51.944740, 4.357085), (51.943821, 4.357853), 
    (51.940529, 4.360508), (51.935448, 4.363258), (51.933723, 4.364162), (51.931461, 4.364682), (51.930069, 4.365018), (51.927929, 4.364900),
    (51.927750, 4.364575), (51.923660, 4.373622), (51.923691, 4.373650), (51.926979, 4.375842), (51.926964, 4.374980), (51.925201, 4.367567),
    (51.952171, 4.530847), (51.875278, 4.354077), (51.875591, 4.354473), (51.875576, 4.355828), (51.875679, 4.357201), (51.876099, 4.357139),
    (51.875980, 4.357467), (51.875481, 4.359515), (51.875500, 4.360422), (51.876122, 4.360257), (51.876011, 4.357473), (51.876289, 4.364535), 
    (51.875854, 4.364359), (51.875870, 4.364915), (51.876083, 4.365851), (51.875942, 4.365623), (51.875790, 4.365723), (51.875648, 4.366027), 
    (51.876381, 4.367132), (51.876099, 4.370345), (51.875874, 4.370180), (51.875591, 4.370445), (51.875851, 4.370840), (51.875900, 4.370735), 
    (51.875980, 4.371172), (51.876152, 4.371324), (51.875969, 4.371545), (51.875710, 4.372345), (51.875019, 4.372492), (51.874519, 4.374115), 
    (51.875801, 4.374798), (51.875881, 4.375285), (51.875381, 4.375182), (51.874733, 4.375641), (51.874264, 4.375369), (51.874111, 4.375957), 
    (51.874420, 4.377025), (51.874538, 4.378173), (51.874840, 4.378160), (51.875648, 4.366023), (51.876019, 4.367993), (51.875889, 4.370208),
    (51.875809, 4.374853), (51.877060, 4.394310), (51.866180, 4.554630), (51.866161, 4.554617), (51.866161, 4.554617), (51.866379, 4.553540), 
    (51.866390, 4.553525), (51.866470, 4.553150), (51.866508, 4.553443), (51.866501, 4.553165), (51.866840, 4.553167), (51.867249, 4.553345), 
    (51.868992, 4.552337), (51.868889, 4.552237), (51.868191, 4.553162), (51.868771, 4.551740), (51.868591, 4.551348), (51.868401, 4.550557), 
    (51.868130, 4.550400), (51.868061, 4.550508), (51.867889, 4.550237), (51.867699, 4.550232), (51.867611, 4.550183), (51.866329, 4.554102), 
    (51.866428, 4.551800), (51.878231, 4.578028), (51.876942, 4.575860), (51.876659, 4.577937), (51.876308, 4.577647), (51.876942, 4.575860), 
    (51.899059, 4.549817), (51.898319, 4.549875), (51.914955, 4.536726), (51.914181, 4.536775), (51.913639, 4.535338), (51.914200, 4.534308), 
    (51.919033, 4.533980), (51.919369, 4.534172), (51.919540, 4.534540), (51.919941, 4.534437), (51.925449, 4.539258), (51.925671, 4.539332), 
    (51.925766, 4.539145), (51.926350, 4.536135), (51.946259, 4.534313), (51.946678, 4.534058), (51.946716, 4.532471), (51.950241, 4.530770), 
    (51.949131, 4.528152), (51.949581, 4.527830), (51.949421, 4.527205), (51.949291, 4.531802), (51.949268, 4.531682), (51.950294, 4.528594), 
    (51.950447, 4.528435), (51.952862, 4.543250), (51.953800, 4.550055), (51.953800, 4.550110), (51.953819, 4.550505), (51.953831, 4.550555), 
    (51.952244, 4.538253), (51.941460, 4.485115), (51.942299, 4.485537), (51.937962, 4.461262), (51.938049, 4.460963), (51.938187, 4.460633), 
    (51.938389, 4.462012), (51.938599, 4.461818), (51.938629, 4.462075), (51.938652, 4.461869), (51.938450, 4.461135), (51.939018, 4.461298), 
    (51.938751, 4.460382), (51.938438, 4.460071), (51.935230, 4.450202), (51.934990, 4.450263), (51.930771, 4.439460), (51.930779, 4.438747), 
    (51.931129, 4.438678), (51.931412, 4.439023), (51.931389, 4.440078), (51.931469, 4.439567), (51.931461, 4.439450), (51.931843, 4.437848), 
    (51.931759, 4.437483), (51.936253, 4.432872), (51.937592, 4.430878), (51.937611, 4.430793), (51.938061, 4.430650), (51.938580, 4.430238), 
    (51.939461, 4.429335), (51.939541, 4.429075), (51.940361, 4.428165), (51.943359, 4.424520), (51.943447, 4.424546), (51.943668, 4.423973), 
    (51.945332, 4.422122), (51.945602, 4.422104), (51.945911, 4.421798), (51.946430, 4.421225), (51.946579, 4.420773), (51.946850, 4.420798), 
    (51.947231, 4.420264), (51.947929, 4.419143), (51.948708, 4.418588), (51.949261, 4.418088), (51.950039, 4.417750), (51.952354, 4.414354),
    (51.951427, 4.414880), (51.952339, 4.421722), (51.952148, 4.421567), (51.950588, 4.415008), (51.950741, 4.415627), (51.950600, 4.415953),
    (51.949940, 4.415242), (51.949924, 4.415112), (51.949699, 4.415435), (51.950840, 4.416965), (51.950539, 4.417313), (51.950569, 4.417713)
    
]
# Select the rows where mask is false
mask = incidents_df.apply(
    lambda row: any(
        abs(row['primaire_locatie_breedtegraad'] - point[0]) < 1e-6 and 
        abs(row['primaire_locatie_lengtegraad'] - point[1]) < 1e-6 for point in exclude_points
    ), axis=1
)

# Filter out the rows to exclude
incidents_df = incidents_df[~mask]
incidents_df = incidents_df.sort_values(by='starttijd')
incidents_df.reset_index(drop=True, inplace=True)
# Unique IDs
unique_id_count = incidents_df['id'].nunique()
print(f'Unique IDs: {unique_id_count}')

incidents_df.tail()


Rows: 24595
Rows: 2395
Rows: 2267
Rows: 2237
Unique IDs: 1904


id           starttijd            eindtijd  \
1899  RWS02_0000188885_188885 2020-05-30 18:45:35 2020-05-30 18:49:36   
1900  RWS02_0000188891_188891 2020-05-30 19:41:36 2020-05-30 19:47:35   
1901   NLRWS_NLSIT002761421_1 2020-05-30 19:44:00 2020-05-30 20:10:24   
1902  RWS02_0000188897_188897 2020-05-30 20:52:36 2020-05-30 21:02:36   
1903  RWS02_0000188900_188900 2020-05-30 21:13:35 2020-05-30 21:16:35   

                     type gedetailleerd_type  primaire_locatie_lengtegraad  \
1899  vehicle_obstruction   emergencyVehicle                      4.590458   
1900  vehicle_obstruction   emergencyVehicle                      4.415205   
1901  general_obstruction    objectOnTheRoad                      4.535378   
1902  vehicle_obstruction   emergencyVehicle                      4.532328   
1903  vehicle_obstruction   emergencyVehicle                      4.439620   

      primaire_locatie_breedtegraad  
1899                      51.862198  
1900                      51.922501  
1901                      51.937969  
1902                      51.950150  
1903                      51.868599

In [160]:
# Calculate the average location for the center of the map
average_latitude = incidents_df['primaire_locatie_breedtegraad'].mean()
average_longitude = incidents_df['primaire_locatie_lengtegraad'].mean()

# Create a map centered around this average location
incidents_map = folium.Map(location=[average_latitude, average_longitude], zoom_start=12)

# Add markers for each incident
for idx, row in incidents_df.iterrows():
    folium.Marker(
        location=[row['primaire_locatie_breedtegraad'], row['primaire_locatie_lengtegraad']],
        popup=(
            f"ID: {row['id']}<br>"
            f"Start: {row['starttijd']}<br>"
            f"End: {row['eindtijd']}<br>"
            f"Type: {row['type']}<br>"
            f"Detail: {row['gedetailleerd_type']}<br>"
            f"Latitude: {row['primaire_locatie_breedtegraad']:.6f}<br>"
            f"Longitude: {row['primaire_locatie_lengtegraad']:.6f}"
        ),
        tooltip='Click for more info'
    ).add_to(incidents_map)

# Save the map or display it in a Jupyter notebook
incidents_map.save('incidents_map.html')
incidents_map

<h1>Visualize both dataframes</h1>

In [161]:

# Initialize the map centered around a general location
m = folium.Map(location=[51.9225, 4.47917], zoom_start=12)  # Example central location for visualization

# Add markers for cameras from unique_rows
for index, row in unique_rows.iterrows():
    folium.Marker(
        location=[row['start_locatie_latitude'], row['start_locatie_longitude']],
        icon=folium.Icon(color='blue', icon='camera'),
        popup=f"Camera Location: {row['id_meetlocatie']}",
    ).add_to(m)

# Add markers for incidents from incidents_df
for index, row in incidents_df.iterrows():
    folium.Marker(
        location=[row['primaire_locatie_breedtegraad'], row['primaire_locatie_lengtegraad']],
        icon=folium.Icon(color='red', icon='info-sign'),
        popup=(
            f"ID: {row['id']}<br>"
            f"Type: {row['type']}<br>"
            f"Detail: {row['gedetailleerd_type']}<br>"
            f"Start: {row['starttijd']}<br>"
            f"End: {row['eindtijd']}"
        ),
    ).add_to(m)

# Display the map in Jupyter Notebook or save it to an HTML file
m.save('combined_map.html')
m

In [11]:
def haversine(lon1, lat1, lon2, lat2):
    # Convert decimal degrees to radians
    lon1, lat1, lon2, lat2 = map(radians, [lon1, lat1, lon2, lat2])

    # Haversine formula
    dlon = lon2 - lon1
    dlat = lat2 - lat1
    a = sin(dlat/2)**2 + cos(lat1) * cos(lat2) * sin(dlon/2)**2
    c = 2 * asin(sqrt(a))
    r = 6371 # Radius of earth in kilometers
    return c * r

def find_nearest(df_a, df_b, threshold_km=1):
    # Initialize columns for storing results
    df_b['nearest_camera_id'] = None
    df_b['distance_to_camera_km'] = np.inf
    
    for i, row in df_b.iterrows():
        # Initialize min distance with a large number
        min_dist = float('inf')
        nearest_camera_id = None
        for j, cam_row in df_a.iterrows():
            dist = haversine(row['primaire_locatie_lengtegraad'], row['primaire_locatie_breedtegraad'],
                             cam_row['start_locatie_longitude'], cam_row['start_locatie_latitude'])
            if dist < min_dist:
                min_dist = dist
                nearest_camera_id = cam_row['id_meetlocatie']
        
        # If the nearest distance found is within the threshold, save it
        if min_dist <= threshold_km:
            df_b.at[i, 'nearest_camera_id'] = nearest_camera_id
            df_b.at[i, 'distance_to_camera_km'] = min_dist

    # Return only the rows with a camera within the threshold distance
    return df_b[df_b['distance_to_camera_km'] <= threshold_km]

incidents_with_nearest_cameras = find_nearest(unique_rows, incidents_df, threshold_km=1)

# Display the first few rows of the modified dataframe to verify the results
incidents_with_nearest_cameras.head()


id           starttijd            eindtijd  \
0  RWS02_0000157162_157162 2020-03-01 03:14:00 2020-03-01 03:17:58   
1  RWS02_0000157163_157163 2020-03-01 03:17:58 2020-03-01 03:20:28   
2  RWS02_0000157179_157179 2020-03-01 07:23:28 2020-03-01 07:25:27   
3  RWS02_0000157186_157186 2020-03-01 08:30:58 2020-03-01 08:31:58   
4  RWS02_0000157188_157188 2020-03-01 08:38:28 2020-03-01 08:39:58   

                  type gedetailleerd_type  primaire_locatie_lengtegraad  \
0  vehicle_obstruction   emergencyVehicle                      4.426262   
1  vehicle_obstruction   emergencyVehicle                      4.420143   
2  vehicle_obstruction   emergencyVehicle                      4.565480   
3  vehicle_obstruction   emergencyVehicle                      4.576188   
4  vehicle_obstruction   emergencyVehicle                      4.366420   

   primaire_locatie_breedtegraad            nearest_camera_id  \
0                      51.870979  RWS01_MONIBAS_0151hrl0533ra   
1                      51.872253  RWS01_MONIBAS_0151hrr0529ra   
2                      51.882229  RWS01_MONIBAS_0160vwy0239ra   
3                      51.871941  RWS01_MONIBAS_0150vwy0643ra   
4                      51.920952  RWS01_MONIBAS_0041hrl0706ra   

   distance_to_camera_km  
0               0.041030  
1               0.016681  
2               0.060111  
3               0.084247  
4               0.022955

In [24]:
from ipyleaflet import Map, Marker, Icon
import ipywidgets as widgets
from IPython.display import display


# Central location for the map
center = (51.9225, 4.47917)

# Create the map
m = Map(center=center, zoom=12)

# Lists to store coordinates
camera_clicked_points = []
incident_clicked_points = []

# Output widget to display list of coordinates
output = widgets.Output()

def handle_camera_click(event=None, id=None, properties=None, **kwargs):
    coords = (properties['location']['lat'], properties['location']['lng'])
    camera_clicked_points.append(coords)
    with output:
        output.clear_output()
        print(f"Clicked on Camera: {coords}")
        print("All Camera points:", camera_clicked_points)

def handle_incident_click(event=None, id=None, properties=None, **kwargs):
    coords = (properties['location']['lat'], properties['location']['lng'])
    incident_clicked_points.append(coords)
    with output:
        output.clear_output()
        print(f"Clicked on Incident: {coords}")
        print("All Incident points:", incident_clicked_points)

# Prepare the camera markers
for _, cam_row in unique_rows.iterrows():
    camera_marker = Marker(
        location=(cam_row['start_locatie_latitude'], cam_row['start_locatie_longitude']),
        draggable=False,
        icon=Icon(icon_url='https://leafletjs.com/examples/custom-icons/leaf-red.png', icon_size=[38, 95], icon_anchor=[22, 94]),
        title=f"Camera ID: {cam_row['id_meetlocatie']}"
    )
    camera_marker.on_click(handle_camera_click)
    m.add_layer(camera_marker)

# Prepare the incident markers
for _, inc_row in incidents_df.iterrows():
    incident_marker = Marker(
        location=(inc_row['primaire_locatie_breedtegraad'], inc_row['primaire_locatie_lengtegraad']),
        draggable=False,
        icon=Icon(color='red'),
        title=f"Incident ID: {inc_row['id']}"
    )
    incident_marker.on_click(handle_incident_click)
    m.add_layer(incident_marker)

# Display the map and the output widget
display(m)

# Note: Saving to HTML does not retain the Python-based interactivity or the output widget functionality
m.save('interactive_map.html')

Map(center=[51.9225, 4.47917], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zo…